In [1]:
import pandas as pd
import numpy as np
import re
from sklearn import metrics
import nltk
from nltk.stem import WordNetLemmatizer
from nltk.stem import SnowballStemmer
from nltk.corpus import stopwords
from sklearn.cluster import AgglomerativeClustering
from sklearn.cluster import KMeans
from sklearn.cluster import DBSCAN
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
from sklearn.metrics import silhouette_score, v_measure_score
from numpy import unique
from numpy import where
from sklearn.mixture import GaussianMixture
from sklearn.manifold import TSNE

lemmatizer = WordNetLemmatizer()
stemmer = SnowballStemmer("english")

def preprocess(x, stop_words):
    x = x.lower()
    x = re.sub('[0-9]|,|\.|/|$|\(|\)|-|\+|:|•', ' ', x)
      
    if stop_words:
        tokens = nltk.word_tokenize(x)
        tokens = [stemmer.stem(lemmatizer.lemmatize(w, 'v')) for w in tokens if not w.lower() in stopwords.words("english")]
        x = " ".join(tokens)
    x = x.strip()
    return x

def vectorizer(text, min_df, max_df):
    vectorizer = TfidfVectorizer(min_df=min_df, max_df=max_df)
    X = vectorizer.fit_transform(text)
    return X, vectorizer.get_feature_names_out()

df = pd.read_csv('./data/concat.txt', header=None)
df.rename(columns = {0:'text'}, inplace = True)
df.drop(1, axis=1, inplace=True)
df['clean'] = df.text.apply(lambda x: preprocess(x, True))
X, terms = vectorizer(df.clean, 5, 0.95)

In [ ]:
pca = PCA(n_components = 2)
Y_pca1 = pca.fit_transform(X.toarray())

In [2]:
pca = PCA(n_components = 2, random_state=10)
Y_pca = pca.fit_transform(X.toarray())

In [ ]:
Y_tsne1 = TSNE(n_components=2).fit_transform(X)

In [3]:
Y_tsne = TSNE(n_components=2, random_state=10).fit_transform(X)

/opt/envs/multi-env/lib/python3.10/site-packages/sklearn/manifold/_t_sne.py:780: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  warnings.warn(
/opt/envs/multi-env/lib/python3.10/site-packages/sklearn/manifold/_t_sne.py:790: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  warnings.warn(


In [ ]:
X_t = KMeans(n_clusters=10).fit_predict(X)
print(f'Random Kmeans in original dataset: {metrics.silhouette_score(X, X_t, metric="euclidean")}')

fig = plt.figure(figsize=(20, 10))
ax = fig.add_subplot(111)
ax.scatter(Y_pca1[:, 0], Y_pca1[:, 1], c=X_t, edgecolor='k', s=50, alpha=0.75)
plt.title(f'Number of clusters: {len(unique(X_t))}')

In [ ]:
X_t = KMeans(n_clusters=10, random_state=10).fit_predict(X)
print(f'Kmeans random state 10 in original dataset: {metrics.silhouette_score(X, X_t, metric="euclidean")}')

fig = plt.figure(figsize=(20, 10))
ax = fig.add_subplot(111)
ax.scatter(Y_tsne2[:, 0], Y_tsne2[:, 1], c=X_t, edgecolor='k', s=50, alpha=0.75)
plt.title(f'Number of clusters: {len(unique(X_t))}')

In [ ]:
X_t = KMeans(n_clusters=10).fit_predict(Y_pca1)
print(f'Kmeans in PCA1: {metrics.silhouette_score(Y_pca1, X_t, metric="euclidean")}')

fig = plt.figure(figsize=(20, 10))
ax = fig.add_subplot(111)
ax.scatter(Y_pca1[:, 0], Y_pca1[:, 1], c=X_t, edgecolor='k', s=50, alpha=0.75)
plt.title(f'Number of clusters: {len(unique(X_t))}')

In [ ]:
X_t = KMeans(n_clusters=10, random_state=10).fit_predict(Y_pca2)
print(f'Kmeans random state 10 in PCA2: {metrics.silhouette_score(Y_pca2, X_t, metric="euclidean")}')

fig = plt.figure(figsize=(20, 10))
ax = fig.add_subplot(111)
ax.scatter(Y_pca2[:, 0], Y_pca2[:, 1], c=X_t, edgecolor='k', s=50, alpha=0.75)
plt.title(f'Number of clusters: {len(unique(X_t))}')

In [ ]:
X_t = KMeans(n_clusters=10).fit_predict(Y_tsne1)
print(f'Kmeans TSNE: {metrics.silhouette_score(Y_tsne1, X_t, metric="euclidean")}')

fig = plt.figure(figsize=(20, 10))
ax = fig.add_subplot(111)
ax.scatter(Y_tsne1[:, 0], Y_tsne1[:, 1], c=X_t, edgecolor='k', s=50, alpha=0.75)
plt.title(f'Number of clusters: {len(unique(X_t))}')

In [ ]:
X_t = KMeans(n_clusters=10, random_state=10).fit_predict(Y_tsne2)
print(f'Kmeans random state 10 in TSN2: {metrics.silhouette_score(Y_tsne2, X_t, metric="euclidean")}')

fig = plt.figure(figsize=(20, 10))
ax = fig.add_subplot(111)
ax.scatter(Y_tsne2[:, 0], Y_tsne2[:, 1], c=X_t, edgecolor='k', s=50, alpha=0.75)
plt.title(f'Number of clusters: {len(unique(X_t))}')

In [ ]:
results = pd.DataFrame()
for m in ['cosine', 'euclidean', 'manhattan']:
    for i in np.arange(start=0.01, stop=5, step=0.001):
        for j in np.arange(start=5, stop=50, step=1):
            res = dbscan_loop(m, i, j, X, False, False)
            res2 = dbscan_loop(m, i, j, Y_pca, True, False)
            res3 = dbscan_loop(m, i, j, Y_tsne, False, True)
        
            if res is not None:
                results = results.append(res)
            if res2 is not None:
                results = results.append(res2)
            if res3 is not None:
                results = results.append(res3)

/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  resul

/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res3)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  r

/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  r

/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  r

/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res2)
/tmp/ipykernel_516377/2878778029.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  r

...

/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  resul

/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  resul

/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  resul

/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  resul

/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(res)
/tmp/ipykernel_516377/2878778029.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  resul

In [ ]:
results

In [ ]:
results.silhouette_euclidian.nlargest(n=10)

In [ ]:
results.silhouette_euclidian.max()

In [4]:
def dbscan_loop(metric, eps, min_samples, X_data, pca, tsne):
    X_t = DBSCAN(metric=metric, eps=eps, min_samples=min_samples).fit_predict(X_data)
    if len(unique(X_t)) > 1:
        silhouette_euclidian = metrics.silhouette_score(X_data, X_t, metric="euclidean")
        try_result = pd.DataFrame(data=[[metric, eps, min_samples, silhouette_euclidian, pca, tsne]],
                                  columns=['metric', 'EPS', 'min_samples', 
                                           'silhouette_euclidian', 'PCA', 'TSNE'])
        
        return try_result
    return None
        #fig = plt.figure(figsize=(20, 10))
        #ax = fig.add_subplot(111)
        #ax.scatter(Y_pca1[:, 0], Y_pca1[:, 1], c=X_t, edgecolor='k', s=50, alpha=0.75)
        #plt.title(f'Number of clusters: {len(unique(X_t))}')

In [ ]:
X_t = dbscan = DBSCAN(metric='euclidean', eps=0.03, min_samples=10).fit_predict(Y_pca1)
print(f'DBSCAN original: {metrics.silhouette_score(Y_pca1, X_t, metric="euclidean")}')

fig = plt.figure(figsize=(20, 10))
ax = fig.add_subplot(111)
ax.scatter(Y_pca1[:, 0], Y_pca1[:, 1], c=X_t, edgecolor='k', s=50, alpha=0.75)
plt.title(f'Number of clusters: {len(unique(X_t))}')

In [ ]:
X_t = dbscan = DBSCAN(metric='euclidean', eps=0.001, min_samples=2).fit_predict(Y_tsne1)
print(f'DBSCAN original: {metrics.silhouette_score(Y_tsne1, X_t, metric="euclidean")}')

fig = plt.figure(figsize=(20, 10))
ax = fig.add_subplot(111)
ax.scatter(Y_tsne1[:, 0], Y_tsne1[:, 1], c=X_t, edgecolor='k', s=50, alpha=0.75)
plt.title(f'Number of clusters: {len(unique(X_t))}')

In [ ]:
n_inits = np.arange(start=10, stop=500, step=10)
for init in n_inits:
    kmeans_fixed_random(init)

for init in n_inits:
    kmeans_random(init)

In [ ]:
def kmeans_fixed_random(n_init):
    X_t = KMeans(n_clusters=10, n_init=n_init, random_state=61659).fit_predict(X)
    print(f'Kmeans fixed random state with n_init {n_init}: {metrics.silhouette_score(X, X_t, metric="euclidean")}')

In [ ]:
def kmeans_random(n_init):
    X_t = KMeans(n_clusters=10, n_init=n_init).fit_predict(X)
    print(f'Random Kmeans with n_init {n_init}: {metrics.silhouette_score(X, X_t, metric="euclidean")}')

In [ ]:
from math import sqrt
def optimal_number_of_clusters(wcss):
    x1, y1 = 2, wcss[0]
    x2, y2 = 30, wcss[len(wcss)-1]

    distances = []
    for i in range(len(wcss)):
        x0 = i+2
        y0 = wcss[i]
        numerator = abs((y2-y1)*x0 - (x2-x1)*y0 + x2*y1 - y2*x1)
        denominator = sqrt((y2 - y1)**2 + (x2 - x1)**2)
        distances.append(numerator/denominator)
    
    return distances.index(max(distances)) + 2

In [ ]:
wcss = []
for i in range(1,30):
    kmeans = KMeans(n_clusters=i, random_state=900)
    kmeans.fit(X)
    wcss.append(kmeans.inertia_)

In [ ]:
optimal_number_of_clusters(wcss)

In [ ]:
'''Plot da curva css'''
plt.plot(range(1,30), wcss)
plt.title('Elbow Method')
plt.xlabel('Number of clusters')
plt.ylabel('WCSS')
plt.show()